# 사용할 라이브러리 로딩

In [116]:
import numpy as np # Numpy
import pandas as pd # Pandas
import matplotlib as mpl #Matplotlib 세팅용
import matplotlib.pyplot as plt # 시각화 도구
import seaborn as sns # 시각화 도구
from sklearn.model_selection import train_test_split # 데이터셋 분리
from sklearn.model_selection import KFold # KFold 교차검증
from sklearn.cluster import KMeans # 클러스터링
from sklearn.metrics import silhouette_score # 실루엣 점수
import xgboost as xgb # XGBoost
from sklearn.model_selection import GridSearchCV # 그리드 서치
from sklearn.metrics import accuracy_score, precision_score # 평가 지표
from sklearn.metrics import recall_score, confusion_matrix, roc_auc_score, f1_score # 평가 지표
from imblearn.combine import SMOTEENN, SMOTETomek # 복합샘플링
from hyperopt import hp, fmin, tpe, Trials # HyperOPT

import warnings # 경고문 제거용


%matplotlib inline
%config Inlinebackend.figure_format = 'retina'

# 한글 폰트 설정
mpl.rc('font', family='D2Coding')
# 유니코드에서 음수 부호 설정
mpl.rc('axes', unicode_minus = False)

warnings.filterwarnings('ignore')
sns.set(font="D2Coding", rc={"axes.unicode_minus":False}, style='darkgrid')
plt.rc('figure', figsize=(10,8))

# 데이터 로딩

In [2]:
data = pd.read_csv('train.csv')

## 데이터 탐색

In [3]:
data.head()

PassengerId HomePlanet CryoSleep  Cabin  Destination   Age    VIP  \
0     0001_01     Europa     False  B/0/P  TRAPPIST-1e  39.0  False   
1     0002_01      Earth     False  F/0/S  TRAPPIST-1e  24.0  False   
2     0003_01     Europa     False  A/0/S  TRAPPIST-1e  58.0   True   
3     0003_02     Europa     False  A/0/S  TRAPPIST-1e  33.0  False   
4     0004_01      Earth     False  F/1/S  TRAPPIST-1e  16.0  False   

   RoomService  FoodCourt  ShoppingMall     Spa  VRDeck               Name  \
0          0.0        0.0           0.0     0.0     0.0    Maham Ofracculy   
1        109.0        9.0          25.0   549.0    44.0       Juanna Vines   
2         43.0     3576.0           0.0  6715.0    49.0      Altark Susent   
3          0.0     1283.0         371.0  3329.0   193.0       Solam Susent   
4        303.0       70.0         151.0   565.0     2.0  Willy Santantines   

   Transported  
0        False  
1         True  
2        False  
3        False  
4         True

In [4]:
data.columns

Index(['PassengerId', 'HomePlanet', 'CryoSleep', 'Cabin', 'Destination', 'Age',
       'VIP', 'RoomService', 'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck',
       'Name', 'Transported'],
      dtype='object')

In [5]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8693 entries, 0 to 8692
Data columns (total 14 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   PassengerId   8693 non-null   object 
 1   HomePlanet    8492 non-null   object 
 2   CryoSleep     8476 non-null   object 
 3   Cabin         8494 non-null   object 
 4   Destination   8511 non-null   object 
 5   Age           8514 non-null   float64
 6   VIP           8490 non-null   object 
 7   RoomService   8512 non-null   float64
 8   FoodCourt     8510 non-null   float64
 9   ShoppingMall  8485 non-null   float64
 10  Spa           8510 non-null   float64
 11  VRDeck        8505 non-null   float64
 12  Name          8493 non-null   object 
 13  Transported   8693 non-null   bool   
dtypes: bool(1), float64(6), object(7)
memory usage: 891.5+ KB


In [6]:
data.isna().sum()

PassengerId       0
HomePlanet      201
CryoSleep       217
Cabin           199
Destination     182
Age             179
VIP             203
RoomService     181
FoodCourt       183
ShoppingMall    208
Spa             183
VRDeck          188
Name            200
Transported       0
dtype: int64

## Cabin 결측값 처리
- 결측값 확인 후 우선 Cabin부터 채워넣기로 함
- PassengerId의 첫 4자리 숫자는 승객의 그룹을 의미함으로 Cabin 결측값 중 그룹이 있으면 그룹의 Cabin으로 채워넣음
- train뿐만 아니라 test에도 결측값이 있기에 같이 처리하기로 함
- 그렇게 처리하고 나온 파일이 하단의 파일

In [7]:
data = pd.read_excel('train_test_origin.xlsx')

In [8]:
data.head()

PassengerId HomePlanet  CryoSleep Cabin1  Cabin2 Combi Cabin3  Cabin  \
0     0001_01     Europa        0.0      B     0.0    B0      P  B/0/P   
1     0002_01      Earth        0.0      F     0.0    F0      S  F/0/S   
2     0003_01     Europa        0.0      A     0.0    A0      S  A/0/S   
3     0003_02     Europa        0.0      A     0.0    A0      S  A/0/S   
4     0004_01      Earth        0.0      F     1.0    F1      S  F/1/S   

   Destination   Age  VIP  RoomService  FoodCourt  ShoppingMall     Spa  \
0  TRAPPIST-1e  39.0  0.0          0.0        0.0           0.0     0.0   
1  TRAPPIST-1e  24.0  0.0        109.0        9.0          25.0   549.0   
2  TRAPPIST-1e  58.0  1.0         43.0     3576.0           0.0  6715.0   
3  TRAPPIST-1e  33.0  0.0          0.0     1283.0         371.0  3329.0   
4  TRAPPIST-1e  16.0  0.0        303.0       70.0         151.0   565.0   

   VRDeck               Name  Transported  
0     0.0    Maham Ofracculy          0.0  
1    44.0       Juanna Vines          1.0  
2    49.0      Altark Susent          0.0  
3   193.0       Solam Susent          0.0  
4     2.0  Willy Santantines          1.0

In [9]:
# 결측값을 처리하면 Cabin을 나눠서 구분함
# Cabin은 섹터/방번호/측면으로 구분되어 있음
# Cabin1은 섹터
# Cabin2는 방번호
# Combi는 Cabin1+Cabin2
# Cabin3는 측면(P(ort)는 좌현, S(tarboard)는 우현)
data.columns

Index(['PassengerId', 'HomePlanet', 'CryoSleep', 'Cabin1', 'Cabin2', 'Combi',
       'Cabin3', 'Cabin', 'Destination', 'Age', 'VIP', 'RoomService',
       'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck', 'Name', 'Transported'],
      dtype='object')

In [10]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12970 entries, 0 to 12969
Data columns (total 18 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   PassengerId   12970 non-null  object 
 1   HomePlanet    12691 non-null  object 
 2   CryoSleep     12660 non-null  float64
 3   Cabin1        12804 non-null  object 
 4   Cabin2        12804 non-null  float64
 5   Combi         12804 non-null  object 
 6   Cabin3        12804 non-null  object 
 7   Cabin         12804 non-null  object 
 8   Destination   12704 non-null  object 
 9   Age           12700 non-null  float64
 10  VIP           12674 non-null  float64
 11  RoomService   12776 non-null  float64
 12  FoodCourt     12752 non-null  float64
 13  ShoppingMall  12760 non-null  float64
 14  Spa           12754 non-null  float64
 15  VRDeck        12766 non-null  float64
 16  Name          12676 non-null  object 
 17  Transported   8693 non-null   float64
dtypes: float64(10), object(8)


- test 데이터는 Kaggle에 제출해야하는 데이터이기에 target인 Transported가 전부 결측임

In [11]:
data.isna().sum()

PassengerId        0
HomePlanet       279
CryoSleep        310
Cabin1           166
Cabin2           166
Combi            166
Cabin3           166
Cabin            166
Destination      266
Age              270
VIP              296
RoomService      194
FoodCourt        218
ShoppingMall     210
Spa              216
VRDeck           204
Name             294
Transported     4277
dtype: int64

- 나머지 결측값을 처리하기 위해 클러스터링을 해보기로 함
- 클러스터링 하기 전에 전처리를 진행해야함

# 전처리

## 필요없는 feature 제거

In [12]:
# 분류하는데 필요없다고 예상되는 'PassengerId', 'Name' feature 제거
data.drop(['PassengerId', 'Name'], inplace=True, axis=1)

In [13]:
# 제거 확인
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12970 entries, 0 to 12969
Data columns (total 16 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    12691 non-null  object 
 1   CryoSleep     12660 non-null  float64
 2   Cabin1        12804 non-null  object 
 3   Cabin2        12804 non-null  float64
 4   Combi         12804 non-null  object 
 5   Cabin3        12804 non-null  object 
 6   Cabin         12804 non-null  object 
 7   Destination   12704 non-null  object 
 8   Age           12700 non-null  float64
 9   VIP           12674 non-null  float64
 10  RoomService   12776 non-null  float64
 11  FoodCourt     12752 non-null  float64
 12  ShoppingMall  12760 non-null  float64
 13  Spa           12754 non-null  float64
 14  VRDeck        12766 non-null  float64
 15  Transported   8693 non-null   float64
dtypes: float64(10), object(6)
memory usage: 1.6+ MB


## CryoSleep, VIP, Cabin3 boolean 타입으로 캐스팅

In [14]:
# Cabin3의 P(좌현)를 False으로 S(우현)를 True로 변경
data['Cabin3'].replace({'P': True,'S': False}, inplace=True)

In [15]:
# boolean으로 변환
data['CryoSleep'] = data['CryoSleep'].astype(bool)
data['VIP'] = data['VIP'].astype(bool)
data['Cabin3'] = data['Cabin3'].astype(bool)

In [16]:
# 변환 확인
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12970 entries, 0 to 12969
Data columns (total 16 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    12691 non-null  object 
 1   CryoSleep     12970 non-null  bool   
 2   Cabin1        12804 non-null  object 
 3   Cabin2        12804 non-null  float64
 4   Combi         12804 non-null  object 
 5   Cabin3        12970 non-null  bool   
 6   Cabin         12804 non-null  object 
 7   Destination   12704 non-null  object 
 8   Age           12700 non-null  float64
 9   VIP           12970 non-null  bool   
 10  RoomService   12776 non-null  float64
 11  FoodCourt     12752 non-null  float64
 12  ShoppingMall  12760 non-null  float64
 13  Spa           12754 non-null  float64
 14  VRDeck        12766 non-null  float64
 15  Transported   8693 non-null   float64
dtypes: bool(3), float64(8), object(5)
memory usage: 1.3+ MB


In [17]:
# target 값을 제외하고 다른 변수에 저장
df = data.iloc[:,:15]

In [18]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12970 entries, 0 to 12969
Data columns (total 15 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    12691 non-null  object 
 1   CryoSleep     12970 non-null  bool   
 2   Cabin1        12804 non-null  object 
 3   Cabin2        12804 non-null  float64
 4   Combi         12804 non-null  object 
 5   Cabin3        12970 non-null  bool   
 6   Cabin         12804 non-null  object 
 7   Destination   12704 non-null  object 
 8   Age           12700 non-null  float64
 9   VIP           12970 non-null  bool   
 10  RoomService   12776 non-null  float64
 11  FoodCourt     12752 non-null  float64
 12  ShoppingMall  12760 non-null  float64
 13  Spa           12754 non-null  float64
 14  VRDeck        12766 non-null  float64
dtypes: bool(3), float64(7), object(5)
memory usage: 1.2+ MB


## 클러스터링을 위해 다른 결측값들을 전부 제거

In [19]:
df.dropna(inplace=True)
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11076 entries, 0 to 12969
Data columns (total 15 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    11076 non-null  object 
 1   CryoSleep     11076 non-null  bool   
 2   Cabin1        11076 non-null  object 
 3   Cabin2        11076 non-null  float64
 4   Combi         11076 non-null  object 
 5   Cabin3        11076 non-null  bool   
 6   Cabin         11076 non-null  object 
 7   Destination   11076 non-null  object 
 8   Age           11076 non-null  float64
 9   VIP           11076 non-null  bool   
 10  RoomService   11076 non-null  float64
 11  FoodCourt     11076 non-null  float64
 12  ShoppingMall  11076 non-null  float64
 13  Spa           11076 non-null  float64
 14  VRDeck        11076 non-null  float64
dtypes: bool(3), float64(7), object(5)
memory usage: 1.1+ MB


## 원핫인코딩

In [20]:
# object 타입의 데이터들 더미화
train_encoding = pd.get_dummies(df['HomePlanet'])
df=df.drop('HomePlanet',axis=1)
df = df.join(train_encoding)

train_encoding = pd.get_dummies(df['Destination'])
df=df.drop('Destination',axis=1)
df = df.join(train_encoding)

train_encoding = pd.get_dummies(df['Cabin1'])
df=df.drop('Cabin1',axis=1)
df = df.join(train_encoding)

In [21]:
# 데이터 확인
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11076 entries, 0 to 12969
Data columns (total 26 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   CryoSleep      11076 non-null  bool   
 1   Cabin2         11076 non-null  float64
 2   Combi          11076 non-null  object 
 3   Cabin3         11076 non-null  bool   
 4   Cabin          11076 non-null  object 
 5   Age            11076 non-null  float64
 6   VIP            11076 non-null  bool   
 7   RoomService    11076 non-null  float64
 8   FoodCourt      11076 non-null  float64
 9   ShoppingMall   11076 non-null  float64
 10  Spa            11076 non-null  float64
 11  VRDeck         11076 non-null  float64
 12  Earth          11076 non-null  uint8  
 13  Europa         11076 non-null  uint8  
 14  Mars           11076 non-null  uint8  
 15  55 Cancri e    11076 non-null  uint8  
 16  PSO J318.5-22  11076 non-null  uint8  
 17  TRAPPIST-1e    11076 non-null  uint8  
 18  A     

## 스케일링

In [22]:
# 스케일링을 위한 함수 생성
col = ['Cabin2', 'Age', 'RoomService','FoodCourt','ShoppingMall','Spa','VRDeck']
def data_scaled(df, col):
    for i in col:
        data_mean = df[i].mean()
        data_std = df[i].std()
        scaled = (df[i]-data_mean)/data_std
        df[i]=scaled
    return df

In [23]:
data_scaled(df, col)

CryoSleep    Cabin2  Combi  Cabin3     Cabin       Age    VIP  \
0          False -1.171058     B0    True     B/0/P  0.707877  False   
1          False -1.171058     F0   False     F/0/S -0.329018  False   
2          False -1.171058     A0   False     A/0/S  2.021278   True   
3          False -1.171058     A0   False     A/0/S  0.293119  False   
4          False -1.169112     F1   False     F/1/S -0.882029  False   
...          ...       ...    ...     ...       ...       ...    ...   
12962       True  1.737845  G1495   False  G/1495/S  0.984383  False   
12963      False -0.630138   D278   False   D/278/S  0.984383  False   
12964      False  2.323517  F1796   False  F/1796/S  0.777004  False   
12965       True  1.739790  G1496   False  G/1496/S  0.362246  False   
12969       True  1.743682  G1498   False  G/1498/S  0.984383  False   

       RoomService  FoodCourt  ShoppingMall  ...  PSO J318.5-22  TRAPPIST-1e  \
0        -0.334616  -0.282674     -0.285975  ...              0            1   
1        -0.166861  -0.277057     -0.244125  ...              0            1   
2        -0.268437   1.949128     -0.285975  ...              0            1   
3        -0.334616   0.518053      0.335083  ...              0            1   
4         0.131712  -0.238987     -0.033199  ...              0            1   
...            ...        ...           ...  ...            ...          ...   
12962    -0.334616  -0.282674     -0.285975  ...              0            1   
12963    -0.262281  -0.282674      6.160647  ...              0            1   
12964    -0.334616   0.257177     -0.285975  ...              0            1   
12965    -0.334616  -0.282674     -0.285975  ...              0            1   
12969    -0.334616  -0.282674     -0.285975  ...              1            0   

       A  B  C  D  E  F  G  T  
0      0  1  0  0  0  0  0  0  
1      0  0  0  0  0  1  0  0  
2      1  0  0  0  0  0  0  0  
3      1  0  0  0  0  0  0  0  
4      0  0  0  0  0  1  0  0  
...   .. .. .. .. .. .. .. ..  
12962  0  0  0  0  0  0  1  0  
12963  0  0  0  1  0  0  0  0  
12964  0  0  0  0  0  1  0  0  
12965  0  0  0  0  0  0  1  0  
12969  0  0  0  0  0  0  1  0  

[11076 rows x 26 columns]

In [24]:
df.head()

CryoSleep    Cabin2 Combi  Cabin3  Cabin       Age    VIP  RoomService  \
0      False -1.171058    B0    True  B/0/P  0.707877  False    -0.334616   
1      False -1.171058    F0   False  F/0/S -0.329018  False    -0.166861   
2      False -1.171058    A0   False  A/0/S  2.021278   True    -0.268437   
3      False -1.171058    A0   False  A/0/S  0.293119  False    -0.334616   
4      False -1.169112    F1   False  F/1/S -0.882029  False     0.131712   

   FoodCourt  ShoppingMall  ...  PSO J318.5-22  TRAPPIST-1e  A  B  C  D  E  F  \
0  -0.282674     -0.285975  ...              0            1  0  1  0  0  0  0   
1  -0.277057     -0.244125  ...              0            1  0  0  0  0  0  1   
2   1.949128     -0.285975  ...              0            1  1  0  0  0  0  0   
3   0.518053      0.335083  ...              0            1  1  0  0  0  0  0   
4  -0.238987     -0.033199  ...              0            1  0  0  0  0  0  1   

   G  T  
0  0  0  
1  0  0  
2  0  0  
3  0  0  
4  0  0  

[5 rows x 26 columns]

## 클러스터링
- 필요없는 feature 추가로 제거한 후 진행

In [25]:
dt = df.drop(['Combi', 'Cabin'], axis=1)

In [26]:
# k_range = range(2,30)

# best_k = -1
# best_silhouette_score = -1

# for k in k_range:
#     km = KMeans(n_clusters = k, random_state=109)
#     km.fit(dt)
#     clusters= km.predict(dt)
    
#     score = silhouette_score(dt, clusters)
    
#     print('k: {}, score: {}'.format(k, score))
#     if score > best_silhouette_score:
#         best_k = k
#         best_silhouette_score = score
        
# print('\n best K: {}, best Score: {}'.format(best_k, best_silhouette_score))

- 군집화를 시켜보니 실루엣 점수가 너무 낮아서 이를 포기하고 feature 별로 분류하여 결측값을 채우기로 함

## CryoSleep 결측값 채우기
- XGBoost 활용하기

In [27]:
dt.CryoSleep.value_counts()

False    6719
True     4357
Name: CryoSleep, dtype: int64

In [28]:
dt.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11076 entries, 0 to 12969
Data columns (total 24 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   CryoSleep      11076 non-null  bool   
 1   Cabin2         11076 non-null  float64
 2   Cabin3         11076 non-null  bool   
 3   Age            11076 non-null  float64
 4   VIP            11076 non-null  bool   
 5   RoomService    11076 non-null  float64
 6   FoodCourt      11076 non-null  float64
 7   ShoppingMall   11076 non-null  float64
 8   Spa            11076 non-null  float64
 9   VRDeck         11076 non-null  float64
 10  Earth          11076 non-null  uint8  
 11  Europa         11076 non-null  uint8  
 12  Mars           11076 non-null  uint8  
 13  55 Cancri e    11076 non-null  uint8  
 14  PSO J318.5-22  11076 non-null  uint8  
 15  TRAPPIST-1e    11076 non-null  uint8  
 16  A              11076 non-null  uint8  
 17  B              11076 non-null  uint8  
 18  C     

### 훈련셋 테스트셋 검증셋 분리

In [29]:
X_train, X_test, y_train, y_test = train_test_split(dt.drop(['CryoSleep'],axis=1),dt.CryoSleep,
                                                    random_state=109)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train)

### 모델 생성(그리드서치)

In [64]:
xgbo = xgb.XGBClassifier()

params = {
    'max_depth':[2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, None],
    'learning_rate':[0.01, 0.05, 0.1, 0.15, 0.2, 0.25, 0.3, 0.35, 0.4],
    'gamma':[0.5, 1, 1.5, 2, 2.5, 3, 3.5, 4, 4.5, 5],
    'random_state':[109]
}

gs = GridSearchCV(xgbo, param_grid = params, cv = 3, refit = True, n_jobs=-1)
gs.fit(X_train, y_train)

GridSearchCV(cv=3,
             estimator=XGBClassifier(base_score=None, booster=None,
                                     callbacks=None, colsample_bylevel=None,
                                     colsample_bynode=None,
                                     colsample_bytree=None,
                                     early_stopping_rounds=None,
                                     enable_categorical=False, eval_metric=None,
                                     feature_types=None, gamma=None,
                                     gpu_id=None, grow_policy=None,
                                     importance_type=None,
                                     interaction_constraints=None,
                                     learning_rate=None,...
                                     missing=nan, monotone_constraints=None,
                                     n_estimators=100, n_jobs=None,
                                     num_parallel_tree=None, predictor=None,
                                     random_state=None, ...),
             n_jobs=-1,
             param_grid={'gamma': [0.5, 1, 1.5, 2, 2.5, 3, 3.5, 4, 4.5, 5],
                         'learning_rate': [0.01, 0.05, 0.1, 0.15, 0.2, 0.25,
                                           0.3, 0.35, 0.4],
                         'max_depth': [2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,
                                       14, 15, 16, 17, 18, 19, 20, 21, 22, 23,
                                       24, 25, None],
                         'random_state': [109]})

### 결과확인

In [65]:
model = gs.best_estimator_
print(model.score(X_train, y_train))
print(model.score(X_test, y_test))
print(model.score(X_val, y_val))

0.9441412520064205
0.9386059949440231
0.9378911892152143


In [66]:
# 최적의 파라미터값
print(gs.best_params_)

{'gamma': 1.5, 'learning_rate': 0.1, 'max_depth': 4, 'random_state': 109}


In [67]:
xgbo = xgb.XGBClassifier(gamma=1.5, learning_rate=0.1, max_depth=4, random_state=109)
xgbo.fit(X_train, y_train)

XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, feature_types=None, gamma=1.5, gpu_id=-1,
              grow_policy='depthwise', importance_type=None,
              interaction_constraints='', learning_rate=0.1, max_bin=256,
              max_cat_threshold=64, max_cat_to_onehot=4, max_delta_step=0,
              max_depth=4, max_leaves=0, min_child_weight=1, missing=nan,
              monotone_constraints='()', n_estimators=100, n_jobs=0,
              num_parallel_tree=1, predictor='auto', random_state=109, ...)

In [68]:
train_pred = xgbo.predict(X_train)
train_proba = xgbo.predict_proba(X_train)

test_pred = xgbo.predict(X_test)
test_proba = xgbo.predict_proba(X_test)

val_pred = xgbo.predict(X_val)
val_proba = xgbo.predict_proba(X_val)

In [69]:
# 평가용 함수
def  get_clf_eval(y_test, pred=None, pred_proba=None):
    confusion = confusion_matrix(y_test, pred)
    accuracy = accuracy_score(y_test, pred)
    precision = precision_score(y_test, pred)
    recall = recall_score(y_test, pred)
    f1 = f1_score(y_test, pred)
#     roc_auc = roc_auc_score(y_test, pred_proba)
    
    print('오차 행렬')
    print(confusion)
 
    print('정확도: {0:.4f}, 정밀도: {1:.4f}, \
    재현율: {2:.4f}, F1: {3:.4f}'.format(accuracy, precision, recall, f1))

#### 훈련셋 평가

In [70]:
get_clf_eval(y_train, train_pred, train_proba)

오차 행렬
[[3589  212]
 [ 136 2293]]
정확도: 0.9441, 정밀도: 0.9154,     재현율: 0.9440, F1: 0.9295


#### 테스트셋 평가

In [71]:
get_clf_eval(y_test, test_pred, test_proba)

오차 행렬
[[1578  108]
 [  62 1021]]
정확도: 0.9386, 정밀도: 0.9043,     재현율: 0.9428, F1: 0.9231


#### 검증셋 평가

In [72]:
get_clf_eval(y_val, val_pred, val_proba)

오차 행렬
[[1151   81]
 [  48  797]]
정확도: 0.9379, 정밀도: 0.9077,     재현율: 0.9432, F1: 0.9251


- CryoSleep XGBoost 모델은 0.93이상의 정확도와 다른 지표도 좋아 결측값 예측에 사용하기로 함

### 결측값 예측

In [73]:
c_na = pd.read_excel('na_slp.xlsx')

In [74]:
c_na.head()

PassengerId HomePlanet  CryoSleep Cabin1  Cabin2 Combi Cabin3   Cabin  \
0     0099_02      Earth        NaN      G    12.0   G12      P  G/12/P   
1     0105_01      Earth        NaN      F    21.0   F21      P  F/21/P   
2     0110_02     Europa        NaN      B     5.0    B5      P   B/5/P   
3     0115_01       Mars        NaN      F    24.0   F24      P  F/24/P   
4     0173_01      Earth        NaN      E    11.0   E11      S  E/11/S   

   Destination   Age  VIP  RoomService  FoodCourt  ShoppingMall  Spa  VRDeck  \
0  TRAPPIST-1e   2.0  0.0          0.0        0.0           0.0  0.0     0.0   
1  TRAPPIST-1e  27.0  0.0          0.0        0.0         570.0  2.0   131.0   
2  TRAPPIST-1e  40.0  0.0          0.0      331.0           0.0  0.0  1687.0   
3  TRAPPIST-1e  26.0  0.0          0.0        0.0           0.0  0.0     0.0   
4  TRAPPIST-1e  58.0  0.0          0.0      985.0           0.0  5.0     0.0   

               Name  Transported  
0  Thewis Connelson          1.0  
1  Carry Cleachrand          0.0  
2   Aldeba Bootious          0.0  
3         Rohs Pead          1.0  
4    Hilip Grifford          1.0

In [75]:
c_na.drop(['PassengerId', 'Name', 'Transported', 'Combi', 'Cabin', 'CryoSleep'], inplace=True, axis=1)

In [76]:
c_na.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 310 entries, 0 to 309
Data columns (total 12 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    305 non-null    object 
 1   Cabin1        306 non-null    object 
 2   Cabin2        306 non-null    float64
 3   Cabin3        306 non-null    object 
 4   Destination   304 non-null    object 
 5   Age           307 non-null    float64
 6   VIP           301 non-null    float64
 7   RoomService   307 non-null    float64
 8   FoodCourt     307 non-null    float64
 9   ShoppingMall  300 non-null    float64
 10  Spa           303 non-null    float64
 11  VRDeck        303 non-null    float64
dtypes: float64(8), object(4)
memory usage: 29.2+ KB


In [77]:
c_na['Cabin3'].replace({'P': 'True','S': 'False'}, inplace=True)

In [78]:
c_na['Cabin3'] = c_na.Cabin3.astype(bool)
c_na['VIP'] = c_na.VIP.astype(bool)
c_na.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 310 entries, 0 to 309
Data columns (total 12 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    305 non-null    object 
 1   Cabin1        306 non-null    object 
 2   Cabin2        306 non-null    float64
 3   Cabin3        310 non-null    bool   
 4   Destination   304 non-null    object 
 5   Age           307 non-null    float64
 6   VIP           310 non-null    bool   
 7   RoomService   307 non-null    float64
 8   FoodCourt     307 non-null    float64
 9   ShoppingMall  300 non-null    float64
 10  Spa           303 non-null    float64
 11  VRDeck        303 non-null    float64
dtypes: bool(2), float64(7), object(3)
memory usage: 24.9+ KB


In [79]:
# object 타입의 데이터들 더미화
train_encoding = pd.get_dummies(c_na['HomePlanet'])
c_na=c_na.drop('HomePlanet',axis=1)
c_na = c_na.join(train_encoding)

train_encoding = pd.get_dummies(c_na['Destination'])
c_na=c_na.drop('Destination',axis=1)
c_na = c_na.join(train_encoding)

train_encoding = pd.get_dummies(c_na['Cabin1'])
c_na=c_na.drop('Cabin1',axis=1)
c_na = c_na.join(train_encoding)

In [80]:
c_na.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 310 entries, 0 to 309
Data columns (total 23 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Cabin2         306 non-null    float64
 1   Cabin3         310 non-null    bool   
 2   Age            307 non-null    float64
 3   VIP            310 non-null    bool   
 4   RoomService    307 non-null    float64
 5   FoodCourt      307 non-null    float64
 6   ShoppingMall   300 non-null    float64
 7   Spa            303 non-null    float64
 8   VRDeck         303 non-null    float64
 9   Earth          310 non-null    uint8  
 10  Europa         310 non-null    uint8  
 11  Mars           310 non-null    uint8  
 12  55 Cancri e    310 non-null    uint8  
 13  PSO J318.5-22  310 non-null    uint8  
 14  TRAPPIST-1e    310 non-null    uint8  
 15  A              310 non-null    uint8  
 16  B              310 non-null    uint8  
 17  C              310 non-null    uint8  
 18  D         

In [81]:
c_na_d = c_na.dropna(axis=0)

In [82]:
col = ['Cabin2', 'Age', 'RoomService','FoodCourt','ShoppingMall','Spa','VRDeck']
data_scaled(c_na, col)

Cabin2  Cabin3       Age    VIP  RoomService  FoodCourt  ShoppingMall  \
0   -1.183897    True -1.800699  False    -0.329359  -0.324266     -0.351021   
1   -1.166462    True -0.116726  False    -0.329359  -0.324266      0.975138   
2   -1.197458    True  0.758940  False    -0.329359  -0.064159     -0.351021   
3   -1.160650    True -0.184085  False    -0.329359  -0.324266     -0.351021   
4   -1.185834    True  1.971401  False    -0.329359   0.449770     -0.351021   
..        ...     ...       ...    ...          ...        ...           ...   
305  2.260524    True -0.588239  False    -0.329359  -0.324266     -0.351021   
306 -0.635657    True -0.116726  False    -0.329359   1.390402     -0.334735   
307       NaN    True  0.826299  False    -0.329359   1.245810     -0.351021   
308  2.233403    True -0.992392  False    -0.329359  -0.324266           NaN   
309 -0.525234    True  0.220068  False    -0.329359  -0.324266     -0.351021   

          Spa    VRDeck  Earth  ...  PSO J318.5-22  TRAPPIST-1e  A  B  C  D  \
0   -0.236142 -0.287000      1  ...              0            1  0  0  0  0   
1   -0.234693 -0.156691      1  ...              0            1  0  0  0  0   
2   -0.236142  1.391106      0  ...              0            1  0  1  0  0   
3   -0.236142 -0.287000      0  ...              0            1  0  0  0  0   
4   -0.232519 -0.287000      1  ...              0            1  0  0  0  0   
..        ...       ...    ...  ...            ...          ... .. .. .. ..   
305 -0.236142 -0.287000      0  ...              0            0  0  0  0  0   
306  1.634807 -0.268100      0  ...              0            1  0  0  1  0   
307  0.505136  0.575429      0  ...              0            1  0  0  0  0   
308  0.761649 -0.258153      1  ...              0            1  0  0  0  0   
309 -0.236142 -0.287000      0  ...              0            0  0  1  0  0   

     E  F  G  T  
0    0  0  1  0  
1    0  1  0  0  
2    0  0  0  0  
3    0  1  0  0  
4    1  0  0  0  
..  .. .. .. ..  
305  0  1  0  0  
306  0  0  0  0  
307  0  0  0  0  
308  0  1  0  0  
309  0  0  0  0  

[310 rows x 23 columns]

In [83]:
c_na.head()

Cabin2  Cabin3       Age    VIP  RoomService  FoodCourt  ShoppingMall  \
0 -1.183897    True -1.800699  False    -0.329359  -0.324266     -0.351021   
1 -1.166462    True -0.116726  False    -0.329359  -0.324266      0.975138   
2 -1.197458    True  0.758940  False    -0.329359  -0.064159     -0.351021   
3 -1.160650    True -0.184085  False    -0.329359  -0.324266     -0.351021   
4 -1.185834    True  1.971401  False    -0.329359   0.449770     -0.351021   

        Spa    VRDeck  Earth  ...  PSO J318.5-22  TRAPPIST-1e  A  B  C  D  E  \
0 -0.236142 -0.287000      1  ...              0            1  0  0  0  0  0   
1 -0.234693 -0.156691      1  ...              0            1  0  0  0  0  0   
2 -0.236142  1.391106      0  ...              0            1  0  1  0  0  0   
3 -0.236142 -0.287000      0  ...              0            1  0  0  0  0  0   
4 -0.232519 -0.287000      1  ...              0            1  0  0  0  0  1   

   F  G  T  
0  0  1  0  
1  1  0  0  
2  0  0  0  
3  1  0  0  
4  0  0  0  

[5 rows x 23 columns]

In [84]:
c_pred = xgbo.predict(c_na)

In [85]:
c_pred = pd.DataFrame(c_pred)

In [86]:
c_pred.value_counts()

0    310
dtype: int64

In [53]:
c_pred.to_csv('c_pred.csv')

## Destination  결측값 채우기

- Destination의 결측값을 채우기 위해선 원핫인코딩 전의 df이 필요함
- 따라서 원본인 data부터 시작해야한다.

### 전처리

In [87]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12970 entries, 0 to 12969
Data columns (total 16 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    12691 non-null  object 
 1   CryoSleep     12970 non-null  bool   
 2   Cabin1        12804 non-null  object 
 3   Cabin2        12804 non-null  float64
 4   Combi         12804 non-null  object 
 5   Cabin3        12970 non-null  bool   
 6   Cabin         12804 non-null  object 
 7   Destination   12704 non-null  object 
 8   Age           12700 non-null  float64
 9   VIP           12970 non-null  bool   
 10  RoomService   12776 non-null  float64
 11  FoodCourt     12752 non-null  float64
 12  ShoppingMall  12760 non-null  float64
 13  Spa           12754 non-null  float64
 14  VRDeck        12766 non-null  float64
 15  Transported   8693 non-null   float64
dtypes: bool(3), float64(8), object(5)
memory usage: 1.3+ MB


In [88]:
# 필요없는 피처들 제거
dest = data.drop(['Combi', 'Cabin', 'Transported'], axis=1)
dest.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12970 entries, 0 to 12969
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   HomePlanet    12691 non-null  object 
 1   CryoSleep     12970 non-null  bool   
 2   Cabin1        12804 non-null  object 
 3   Cabin2        12804 non-null  float64
 4   Cabin3        12970 non-null  bool   
 5   Destination   12704 non-null  object 
 6   Age           12700 non-null  float64
 7   VIP           12970 non-null  bool   
 8   RoomService   12776 non-null  float64
 9   FoodCourt     12752 non-null  float64
 10  ShoppingMall  12760 non-null  float64
 11  Spa           12754 non-null  float64
 12  VRDeck        12766 non-null  float64
dtypes: bool(3), float64(7), object(3)
memory usage: 1.0+ MB


In [89]:
# object 타입의 데이터들 더미화
train_encoding = pd.get_dummies(dest['HomePlanet'])
dest=dest.drop('HomePlanet',axis=1)
dest = dest.join(train_encoding)

train_encoding = pd.get_dummies(dest['Cabin1'])
dest=dest.drop('Cabin1',axis=1)
dest = dest.join(train_encoding)

In [90]:
dest.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 12970 entries, 0 to 12969
Data columns (total 22 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   CryoSleep     12970 non-null  bool   
 1   Cabin2        12804 non-null  float64
 2   Cabin3        12970 non-null  bool   
 3   Destination   12704 non-null  object 
 4   Age           12700 non-null  float64
 5   VIP           12970 non-null  bool   
 6   RoomService   12776 non-null  float64
 7   FoodCourt     12752 non-null  float64
 8   ShoppingMall  12760 non-null  float64
 9   Spa           12754 non-null  float64
 10  VRDeck        12766 non-null  float64
 11  Earth         12970 non-null  uint8  
 12  Europa        12970 non-null  uint8  
 13  Mars          12970 non-null  uint8  
 14  A             12970 non-null  uint8  
 15  B             12970 non-null  uint8  
 16  C             12970 non-null  uint8  
 17  D             12970 non-null  uint8  
 18  E             12970 non-nu

In [91]:
dest.dropna(axis=0, inplace=True)

In [92]:
dest.isna().sum()

CryoSleep       0
Cabin2          0
Cabin3          0
Destination     0
Age             0
VIP             0
RoomService     0
FoodCourt       0
ShoppingMall    0
Spa             0
VRDeck          0
Earth           0
Europa          0
Mars            0
A               0
B               0
C               0
D               0
E               0
F               0
G               0
T               0
dtype: int64

In [93]:
dest.Destination.unique()

array(['TRAPPIST-1e', 'PSO J318.5-22', '55 Cancri e'], dtype=object)

In [94]:
# Object 타입을 숫자형으로 변경하기
# 'TRAPPIST-1e' = 0, 'PSO J318.5-22' = 1, '55 Cancri e' = 2
dest.Destination.replace({'TRAPPIST-1e':0, 'PSO J318.5-22':1, '55 Cancri e':2}, inplace=True)

- 값들의 개수를 확인해보니 TRAPPIST-1e가 너무 많음 복합샘플링을 해보기로 함

### 복합샘플링

In [96]:
from imblearn.combine import *

In [178]:
X = dest.drop('Destination', axis=1)
y = dest.Destination

In [179]:
X.shape

(11320, 21)

#### SMOTE+ENN

In [101]:
X_samp, y_samp = SMOTEENN(random_state=109).fit_resample(X, y)

In [102]:
X_samp.shape

(11865, 21)

In [95]:
dest.Destination.value_counts()

0    7894
2    2370
1    1056
Name: Destination, dtype: int64

In [105]:
y_samp.value_counts()

1    5408
2    4371
0    2086
Name: Destination, dtype: int64

#### 훈련셋 테스트셋 검증셋 분리

In [158]:
X_train, X_test, y_train, y_test = train_test_split(X_samp, y_samp, random_state=109)

#### HyperOPT

- 하이퍼파라미터가 많을수록 그리드서치는 느려지기에 HyperOPT 사용

In [110]:
# max_depth=??
xgb_search_space = {'max_depth': hp.quniform('max_depth', 5, 15, 1),
                   'min_child_weight': hp.quniform('min_child_weight', 1, 6, 1),
                   'colsample_bytree': hp.uniform('colsample_bytree', 0.5, 0.95),
                   'learning_rate': hp.uniform('learning_rate', 0.01, 0.4),
                   'gamma': hp.uniform('gamma', 0.1, 4)}

In [187]:
# fmin()에서 호출 시 search_space 값으로 XGBClassifier 교차 검증 학습 후 -1 * roc_auc 평균 값을 반환
def objective_func(search_space):
    xgb_clf = xgb.XGBClassifier(n_estimators=100, max_depth=int(search_space['max_depth']),
                            min_child_weight=int(search_space['min_child_weight']),
                            colsapmple_bytree=search_space['colsample_bytree'],
                            learning_rate=search_space['learning_rate'],
                            gamma=search_space['gamma'])
    
    # 3개 k-fold 방식으로 평가된 roc_auc 지표를 담는 list
    roc_auc_list = []
    
    # 3개 k-fold 방식 적용
    kf = KFold(n_splits=3)
    
    # X_train을 다시 학습과 검증용 데이터로 분리
    for tr_index, val_index in kf.split(X_train):
        # kf.split(X_train)으로 추출된 학습과 검증 index 값으로 학습과 검증 데이터 세트 분리
        X_tr, y_tr = X_train.iloc[tr_index], y_train.iloc[tr_index]
        X_val, y_val = X_train.iloc[val_index], y_train.iloc[val_index]
        
        # early stopping은 30회로 설정하고 추출된 학습과 검증 데이터로 XGBClassifier 학습 수행
        xgb_clf.fit(X_tr, y_tr, early_stopping_rounds=30, eval_metric="auc",
                   eval_set=[(X_tr, y_tr), (X_val, y_val)])
        
        # 1로 예측한 확률값 추출 후 roc auc 계산하고 평균 roc auc 계산을 위해 list에 결과값 담음.
        score = roc_auc_score(y_val, xgb_clf.predict_proba(X_val)[:,:], multi_class='ovr')
        roc_auc_list.append(score)
        
    # 3개 k-fold로 계산된 roc_auc 값의 평균값을 반환하되,
    # HyperOPT는 목적함수의 최솟값을 위한 입력값을 찾으므로 -1을 곱한 뒤 반환
    return -1*np.mean(roc_auc_list)

In [140]:
trials = Trials()

# fmin() 함수를 호출. max_evals 지정된 횟수만큼 반복 후 목적함수의 최솟값을 가지는 최적 입력값 추출
best = fmin(fn=objective_func,
           space=xgb_search_space,
           algo=tpe.suggest,
           max_evals=50, # 최대 반복 횟수를 지정합니다
           trials=trials, rstate=np.random.default_rng(seed=109))

print('best:', best)

[12:47:30] WARNING: C:/buildkite-agent/builds/buildkite-windows-cpu-autoscaling-group-i-03de431ba26204c4d-1/xgboost/xgboost-ci-windows/src/learner.cc:767: 
Parameters: { "colsapmple_bytree", "n_estimatiors" } are not used.

[0]	validation_0-auc:0.95229	validation_1-auc:0.91256                                                                  
[1]	validation_0-auc:0.96025	validation_1-auc:0.92181                                                                  
[2]	validation_0-auc:0.96333	validation_1-auc:0.92524                                                                  
[3]	validation_0-auc:0.96682	validation_1-auc:0.92747                                                                  
[4]	validation_0-auc:0.96857	validation_1-auc:0.92969                                                                  
[5]	validation_0-auc:0.96993	validation_1-auc:0.93099                                                                  
[6]	validation_0-auc:0.97059	validation_1-auc:0.93162   

[6]	validation_0-auc:0.97068	validation_1-auc:0.93577                                                                  
[7]	validation_0-auc:0.97196	validation_1-auc:0.93762                                                                  
[8]	validation_0-auc:0.97425	validation_1-auc:0.93959                                                                  
[9]	validation_0-auc:0.97567	validation_1-auc:0.94117                                                                  
[10]	validation_0-auc:0.97664	validation_1-auc:0.94246                                                                 
[11]	validation_0-auc:0.97706	validation_1-auc:0.94273                                                                 
[12]	validation_0-auc:0.97850	validation_1-auc:0.94438                                                                 
[13]	validation_0-auc:0.97934	validation_1-auc:0.94504                                                                 
[14]	validation_0-auc:0.98014	validation

[23]	validation_0-auc:0.98351	validation_1-auc:0.95390                                                                 
[24]	validation_0-auc:0.98391	validation_1-auc:0.95449                                                                 
[25]	validation_0-auc:0.98417	validation_1-auc:0.95450                                                                 
[26]	validation_0-auc:0.98425	validation_1-auc:0.95471                                                                 
[27]	validation_0-auc:0.98425	validation_1-auc:0.95471                                                                 
[28]	validation_0-auc:0.98425	validation_1-auc:0.95471                                                                 
[29]	validation_0-auc:0.98425	validation_1-auc:0.95471                                                                 
[30]	validation_0-auc:0.98425	validation_1-auc:0.95471                                                                 
[31]	validation_0-auc:0.98425	validation

[32]	validation_0-auc:0.96267	validation_1-auc:0.92729                                                                 
[33]	validation_0-auc:0.96327	validation_1-auc:0.92785                                                                 
[34]	validation_0-auc:0.96379	validation_1-auc:0.92817                                                                 
[35]	validation_0-auc:0.96420	validation_1-auc:0.92848                                                                 
[36]	validation_0-auc:0.96469	validation_1-auc:0.92862                                                                 
[37]	validation_0-auc:0.96500	validation_1-auc:0.92890                                                                 
[38]	validation_0-auc:0.96528	validation_1-auc:0.92887                                                                 
[39]	validation_0-auc:0.96600	validation_1-auc:0.92959                                                                 
[40]	validation_0-auc:0.96651	validation

[12:47:35] WARNING: C:/buildkite-agent/builds/buildkite-windows-cpu-autoscaling-group-i-03de431ba26204c4d-1/xgboost/xgboost-ci-windows/src/learner.cc:767: 
Parameters: { "colsapmple_bytree", "n_estimatiors" } are not used.

[0]	validation_0-auc:0.91903	validation_1-auc:0.89229                                                                  
[1]	validation_0-auc:0.92427	validation_1-auc:0.89661                                                                  
[2]	validation_0-auc:0.92855	validation_1-auc:0.90075                                                                  
[3]	validation_0-auc:0.93080	validation_1-auc:0.90330                                                                  
[4]	validation_0-auc:0.93302	validation_1-auc:0.90440                                                                  
[5]	validation_0-auc:0.93496	validation_1-auc:0.90560                                                                  
[6]	validation_0-auc:0.93607	validation_1-auc:0.90613   

...

[59]	validation_0-auc:0.99998	validation_1-auc:0.97160                                                                 
[60]	validation_0-auc:0.99998	validation_1-auc:0.97168                                                                 
[61]	validation_0-auc:0.99998	validation_1-auc:0.97176                                                                 
[62]	validation_0-auc:0.99998	validation_1-auc:0.97179                                                                 
[63]	validation_0-auc:0.99998	validation_1-auc:0.97189                                                                 
[64]	validation_0-auc:0.99998	validation_1-auc:0.97195                                                                 
[65]	validation_0-auc:0.99999	validation_1-auc:0.97203                                                                 
[66]	validation_0-auc:0.99999	validation_1-auc:0.97205                                                                 
[67]	validation_0-auc:0.99999	validation

[26]	validation_0-auc:0.99421	validation_1-auc:0.95480                                                                 
[27]	validation_0-auc:0.99435	validation_1-auc:0.95505                                                                 
[28]	validation_0-auc:0.99460	validation_1-auc:0.95533                                                                 
[29]	validation_0-auc:0.99468	validation_1-auc:0.95554                                                                 
[30]	validation_0-auc:0.99473	validation_1-auc:0.95556                                                                 
[31]	validation_0-auc:0.99490	validation_1-auc:0.95583                                                                 
[32]	validation_0-auc:0.99508	validation_1-auc:0.95622                                                                 
[33]	validation_0-auc:0.99527	validation_1-auc:0.95648                                                                 
[34]	validation_0-auc:0.99540	validation

[14]	validation_0-auc:0.99182	validation_1-auc:0.95402                                                                 
[15]	validation_0-auc:0.99232	validation_1-auc:0.95486                                                                 
[16]	validation_0-auc:0.99285	validation_1-auc:0.95561                                                                 
[17]	validation_0-auc:0.99323	validation_1-auc:0.95642                                                                 
[18]	validation_0-auc:0.99335	validation_1-auc:0.95666                                                                 
[19]	validation_0-auc:0.99375	validation_1-auc:0.95744                                                                 
[20]	validation_0-auc:0.99395	validation_1-auc:0.95774                                                                 
[21]	validation_0-auc:0.99409	validation_1-auc:0.95796                                                                 
[22]	validation_0-auc:0.99426	validation

[2]	validation_0-auc:0.97725	validation_1-auc:0.94179                                                                  
[3]	validation_0-auc:0.98033	validation_1-auc:0.94457                                                                  
[4]	validation_0-auc:0.98244	validation_1-auc:0.94702                                                                  
[5]	validation_0-auc:0.98366	validation_1-auc:0.94906                                                                  
[6]	validation_0-auc:0.98479	validation_1-auc:0.95015                                                                  
[7]	validation_0-auc:0.98599	validation_1-auc:0.95195                                                                  
[8]	validation_0-auc:0.98658	validation_1-auc:0.95219                                                                  
[9]	validation_0-auc:0.98741	validation_1-auc:0.95265                                                                  
[10]	validation_0-auc:0.98765	validation

100%|███████████████████████████████████████████████| 50/50 [06:38<00:00,  7.97s/trial, best loss: -0.9671935359411724]
best: {'colsample_bytree': 0.7458564543464659, 'gamma': 0.1340433243883299, 'learning_rate': 0.3737581747422525, 'max_depth': 13.0, 'min_child_weight': 1.0}


#### 최적합 모델 생성

In [185]:
xgb_clf = xgb.XGBClassifier(colsample_bytree=0.7458564543464659, gamma=0.1340433243883299,
                            learning_rate=0.3737581747422525, max_depth=13,
                            min_child_weight=1.0,random_state=109)
xgb_clf.fit(X_train, y_train)

XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1,
              colsample_bytree=0.7458564543464659, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.1340433243883299, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.3737581747422525, max_bin=256,
              max_cat_threshold=64, max_cat_to_onehot=4, max_delta_step=0,
              max_depth=13, max_leaves=0, min_child_weight=1.0, missing=nan,
              monotone_constraints='()', n_estimators=100, n_jobs=0,
              num_parallel_tree=1, objective='multi:softprob', predictor='auto', ...)

In [186]:
train_pred = xgb_clf.predict(X_train)
train_proba = xgb_clf.predict_proba(X_train)

test_pred = xgb_clf.predict(X_test)
test_proba = xgb_clf.predict_proba(X_test)

#### 결과확인

##### 훈련셋 평가

In [164]:
confusion_matrix(y_train, train_pred)

array([[1038,  357,  189],
       [  57, 3778,  176],
       [ 139,  582, 2582]], dtype=int64)

In [165]:
accuracy_score(y_train, train_pred)

0.8314227916385705

In [176]:
recall_score(y_train, train_pred, labels=[0, 1, 2], average='micro')

0.8314227916385705

In [177]:
precision_score(y_train, train_pred, labels=[0, 1, 2], average='micro')

0.8314227916385705

In [169]:
pcs1 = 1038/(1038+57+139)
pcs2 = 3778/(357+3778+582)
pcs3 = 2582/(189+176+2582)
print('정밀도:',(pcs1+pcs2+pcs3)/3)

정밀도: 0.839414988499836


In [170]:
rc1 = 1038/(1038+357+189)
rc2 = 3778/(3778+57+176)
rc3 = 2582/(2582+582+139)
print('재현도:', (rc1+rc2+rc3)/3)

재현도: 0.7929754573993986


##### 테스트셋 평가

In [166]:
confusion_matrix(y_test, test_pred)

array([[ 298,  126,   78],
       [  30, 1295,   72],
       [  55,  207,  806]], dtype=int64)

In [167]:
accuracy_score(y_test, test_pred)

0.8085608358611392

#### SMOTE+Tomek

In [180]:
X_samp, y_samp = SMOTETomek(random_state=109).fit_resample(X, y)

In [182]:
y.value_counts()

0    7894
2    2370
1    1056
Name: Destination, dtype: int64

In [181]:
y_samp.value_counts()

1    7433
2    7333
0    7072
Name: Destination, dtype: int64

#### 훈련셋 테스트셋 검증셋 분리

In [183]:
X_train, X_test, y_train, y_test = train_test_split(X_samp, y_samp, random_state=109)

#### HyperOPT

In [184]:
trials = Trials()

# fmin() 함수를 호출. max_evals 지정된 횟수만큼 반복 후 목적함수의 최솟값을 가지는 최적 입력값 추출
best = fmin(fn=objective_func,
           space=xgb_search_space,
           algo=tpe.suggest,
           max_evals=50, # 최대 반복 횟수를 지정합니다
           trials=trials, rstate=np.random.default_rng(seed=109))

print('best:', best)

[17:49:32] WARNING: C:/buildkite-agent/builds/buildkite-windows-cpu-autoscaling-group-i-03de431ba26204c4d-1/xgboost/xgboost-ci-windows/src/learner.cc:767: 
Parameters: { "colsapmple_bytree", "n_estimatiors" } are not used.

[0]	validation_0-auc:0.91368	validation_1-auc:0.86312                                                                  
[1]	validation_0-auc:0.92148	validation_1-auc:0.87050                                                                  
[2]	validation_0-auc:0.92726	validation_1-auc:0.87498                                                                  
[3]	validation_0-auc:0.93150	validation_1-auc:0.88005                                                                  
[4]	validation_0-auc:0.93431	validation_1-auc:0.88253                                                                  
[5]	validation_0-auc:0.93728	validation_1-auc:0.88476                                                                  
[6]	validation_0-auc:0.93928	validation_1-auc:0.88688   

[1]	validation_0-auc:0.91771	validation_1-auc:0.87335                                                                  
[2]	validation_0-auc:0.92334	validation_1-auc:0.87926                                                                  
[3]	validation_0-auc:0.92946	validation_1-auc:0.88569                                                                  
[4]	validation_0-auc:0.93239	validation_1-auc:0.88789                                                                  
[5]	validation_0-auc:0.93496	validation_1-auc:0.88985                                                                  
[6]	validation_0-auc:0.93699	validation_1-auc:0.89148                                                                  
[7]	validation_0-auc:0.94047	validation_1-auc:0.89383                                                                  
[8]	validation_0-auc:0.94262	validation_1-auc:0.89540                                                                  
[9]	validation_0-auc:0.94494	validation_

[0]	validation_0-auc:0.91180	validation_1-auc:0.86479                                                                  
[1]	validation_0-auc:0.92150	validation_1-auc:0.87406                                                                  
[2]	validation_0-auc:0.92742	validation_1-auc:0.87811                                                                  
[3]	validation_0-auc:0.92981	validation_1-auc:0.88061                                                                  
[4]	validation_0-auc:0.93402	validation_1-auc:0.88385                                                                  
[5]	validation_0-auc:0.93539	validation_1-auc:0.88522                                                                  
[6]	validation_0-auc:0.93706	validation_1-auc:0.88687                                                                  
[7]	validation_0-auc:0.93954	validation_1-auc:0.88855                                                                  
[8]	validation_0-auc:0.94279	validation_

[2]	validation_0-auc:0.87924	validation_1-auc:0.84860                                                                  
[3]	validation_0-auc:0.88105	validation_1-auc:0.85075                                                                  
[4]	validation_0-auc:0.88259	validation_1-auc:0.85212                                                                  
[5]	validation_0-auc:0.88414	validation_1-auc:0.85319                                                                  
[6]	validation_0-auc:0.88578	validation_1-auc:0.85500                                                                  
[7]	validation_0-auc:0.88757	validation_1-auc:0.85584                                                                  
[8]	validation_0-auc:0.88941	validation_1-auc:0.85712                                                                  
[9]	validation_0-auc:0.89091	validation_1-auc:0.85864                                                                  
[10]	validation_0-auc:0.89166	validation

[70]	validation_0-auc:0.93943	validation_1-auc:0.88993                                                                 
[71]	validation_0-auc:0.94033	validation_1-auc:0.89063                                                                 
[72]	validation_0-auc:0.94068	validation_1-auc:0.89088                                                                 
[73]	validation_0-auc:0.94176	validation_1-auc:0.89190                                                                 
[74]	validation_0-auc:0.94240	validation_1-auc:0.89226                                                                 
[75]	validation_0-auc:0.94271	validation_1-auc:0.89248                                                                 
[76]	validation_0-auc:0.94352	validation_1-auc:0.89327                                                                 
[77]	validation_0-auc:0.94419	validation_1-auc:0.89371                                                                 
[78]	validation_0-auc:0.94458	validation

...

[59]	validation_0-auc:0.99160	validation_1-auc:0.91876                                                                 
[60]	validation_0-auc:0.99186	validation_1-auc:0.91926                                                                 
[61]	validation_0-auc:0.99199	validation_1-auc:0.91943                                                                 
[62]	validation_0-auc:0.99209	validation_1-auc:0.91960                                                                 
[63]	validation_0-auc:0.99232	validation_1-auc:0.91988                                                                 
[64]	validation_0-auc:0.99244	validation_1-auc:0.91998                                                                 
[65]	validation_0-auc:0.99265	validation_1-auc:0.92015                                                                 
[66]	validation_0-auc:0.99274	validation_1-auc:0.92038                                                                 
[67]	validation_0-auc:0.99281	validation

[25]	validation_0-auc:0.96926	validation_1-auc:0.90710                                                                 
[26]	validation_0-auc:0.96969	validation_1-auc:0.90742                                                                 
[27]	validation_0-auc:0.97007	validation_1-auc:0.90783                                                                 
[28]	validation_0-auc:0.97038	validation_1-auc:0.90817                                                                 
[29]	validation_0-auc:0.97075	validation_1-auc:0.90833                                                                 
[30]	validation_0-auc:0.97146	validation_1-auc:0.90937                                                                 
[31]	validation_0-auc:0.97216	validation_1-auc:0.90993                                                                 
[32]	validation_0-auc:0.97247	validation_1-auc:0.91035                                                                 
[33]	validation_0-auc:0.97274	validation

[18]	validation_0-auc:0.96759	validation_1-auc:0.90781                                                                 
[19]	validation_0-auc:0.96804	validation_1-auc:0.90815                                                                 
[20]	validation_0-auc:0.96862	validation_1-auc:0.90881                                                                 
[21]	validation_0-auc:0.96897	validation_1-auc:0.90924                                                                 
[22]	validation_0-auc:0.96911	validation_1-auc:0.90938                                                                 
[23]	validation_0-auc:0.96976	validation_1-auc:0.91037                                                                 
[24]	validation_0-auc:0.97025	validation_1-auc:0.91097                                                                 
[25]	validation_0-auc:0.97061	validation_1-auc:0.91131                                                                 
[26]	validation_0-auc:0.97118	validation

[20]	validation_0-auc:0.96622	validation_1-auc:0.90495                                                                 
[21]	validation_0-auc:0.96712	validation_1-auc:0.90596                                                                 
[22]	validation_0-auc:0.96756	validation_1-auc:0.90630                                                                 
[23]	validation_0-auc:0.96766	validation_1-auc:0.90654                                                                 
[24]	validation_0-auc:0.96787	validation_1-auc:0.90679                                                                 
[25]	validation_0-auc:0.96802	validation_1-auc:0.90714                                                                 
[26]	validation_0-auc:0.96834	validation_1-auc:0.90731                                                                 
[27]	validation_0-auc:0.96878	validation_1-auc:0.90783                                                                 
[28]	validation_0-auc:0.96952	validation

[88]	validation_0-auc:0.97475	validation_1-auc:0.91456                                                                 
[89]	validation_0-auc:0.97475	validation_1-auc:0.91456                                                                 
100%|███████████████████████████████████████████████| 50/50 [11:36<00:00, 13.92s/trial, best loss: -0.9327235174629932]
best: {'colsample_bytree': 0.7509517286334861, 'gamma': 0.11238303917591316, 'learning_rate': 0.37018445848424064, 'max_depth': 13.0, 'min_child_weight': 1.0}


#### 최적합 모델 생성

In [ ]:
xgb_clf = xgb.XGBClassifier(colsample_bytree=0.7458564543464659, gamma=0.1340433243883299,
                            learning_rate=0.3737581747422525, max_depth=13,
                            min_child_weight=1.0,random_state=109)
xgb_clf.fit(X_train, y_train)

## VIP 추가

In [142]:
X_v = dt.drop('VIP', axis=1)
y_v = dt.VIP

In [144]:
X_v.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 11076 entries, 0 to 12969
Data columns (total 23 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   CryoSleep      11076 non-null  bool   
 1   Cabin2         11076 non-null  float64
 2   Cabin3         11076 non-null  bool   
 3   Age            11076 non-null  float64
 4   RoomService    11076 non-null  float64
 5   FoodCourt      11076 non-null  float64
 6   ShoppingMall   11076 non-null  float64
 7   Spa            11076 non-null  float64
 8   VRDeck         11076 non-null  float64
 9   Earth          11076 non-null  uint8  
 10  Europa         11076 non-null  uint8  
 11  Mars           11076 non-null  uint8  
 12  55 Cancri e    11076 non-null  uint8  
 13  PSO J318.5-22  11076 non-null  uint8  
 14  TRAPPIST-1e    11076 non-null  uint8  
 15  A              11076 non-null  uint8  
 16  B              11076 non-null  uint8  
 17  C              11076 non-null  uint8  
 18  D     

In [147]:
y_v

0        False
1        False
2         True
3        False
4        False
         ...  
12962    False
12963    False
12964    False
12965    False
12969    False
Name: VIP, Length: 11076, dtype: bool

In [143]:
X_vsamp, y_vsamp = SMOTEENN(random_state=109).fit_resample(X_v, y_v)

In [150]:
y_v.shape

(11076,)

In [153]:
y_v.value_counts()

False    10584
True       492
Name: VIP, dtype: int64

In [148]:
X_train, X_test, y_train, y_test = train_test_split(X_vsamp, y_vsamp, random_state=109)

In [151]:
# fmin()에서 호출 시 search_space 값으로 XGBClassifier 교차 검증 학습 후 -1 * roc_auc 평균 값을 반환
def bin_objective_func(search_space):
    xgb_clf = xgb.XGBClassifier(n_estimatiors=100, max_depth=int(search_space['max_depth']),
                            min_child_weight=int(search_space['min_child_weight']),
                            colsapmple_bytree=search_space['colsample_bytree'],
                            learning_rate=search_space['learning_rate'],
                            gamma=search_space['gamma'])
    
    # 3개 k-fold 방식으로 평가된 roc_auc 지표를 담는 list
    roc_auc_list = []
    
    # 3개 k-fold 방식 적용
    kf = KFold(n_splits=3)
    
    # X_train을 다시 학습과 검증용 데이터로 분리
    for tr_index, val_index in kf.split(X_train):
        # kf.split(X_train)으로 추출된 학습과 검증 index 값으로 학습과 검증 데이터 세트 분리
        X_tr, y_tr = X_train.iloc[tr_index], y_train.iloc[tr_index]
        X_val, y_val = X_train.iloc[val_index], y_train.iloc[val_index]
        
        # early stopping은 30회로 설정하고 추출된 학습과 검증 데이터로 XGBClassifier 학습 수행
        xgb_clf.fit(X_tr, y_tr, early_stopping_rounds=30, eval_metric="auc",
                   eval_set=[(X_tr, y_tr), (X_val, y_val)])
        
        # 1로 예측한 확률값 추출 후 roc auc 계산하고 평균 roc auc 계산을 위해 list에 결과값 담음.
        score = roc_auc_score(y_val, xgb_clf.predict_proba(X_val)[:,1])
        roc_auc_list.append(score)
        
    # 3개 k-fold로 계산된 roc_auc 값의 평균값을 반환하되,
    # HyperOPT는 목적함수의 최솟값을 위한 입력값을 찾으므로 -1을 곱한 뒤 반환
    return -1*np.mean(roc_auc_list)

In [152]:
trials = Trials()

# fmin() 함수를 호출. max_evals 지정된 횟수만큼 반복 후 목적함수의 최솟값을 가지는 최적 입력값 추출
best = fmin(fn=bin_objective_func,
           space=xgb_search_space,
           algo=tpe.suggest,
           max_evals=50, # 최대 반복 횟수를 지정합니다
           trials=trials, rstate=np.random.default_rng(seed=109))

print('best:', best)

[14:32:38] WARNING: C:/buildkite-agent/builds/buildkite-windows-cpu-autoscaling-group-i-03de431ba26204c4d-1/xgboost/xgboost-ci-windows/src/learner.cc:767: 
Parameters: { "colsapmple_bytree", "n_estimatiors" } are not used.

[0]	validation_0-auc:0.94461	validation_1-auc:0.90766                                                                  
[1]	validation_0-auc:0.96628	validation_1-auc:0.93087                                                                  
[2]	validation_0-auc:0.97725	validation_1-auc:0.94611                                                                  
[3]	validation_0-auc:0.98217	validation_1-auc:0.95453                                                                  
[4]	validation_0-auc:0.98627	validation_1-auc:0.96305                                                                  
[5]	validation_0-auc:0.98798	validation_1-auc:0.96530                                                                  
[6]	validation_0-auc:0.98966	validation_1-auc:0.96852   

[66]	validation_0-auc:0.99877	validation_1-auc:0.99036                                                                 
[67]	validation_0-auc:0.99877	validation_1-auc:0.99036                                                                 
[68]	validation_0-auc:0.99877	validation_1-auc:0.99036                                                                 
[14:32:39] WARNING: C:/buildkite-agent/builds/buildkite-windows-cpu-autoscaling-group-i-03de431ba26204c4d-1/xgboost/xgboost-ci-windows/src/learner.cc:767: 
Parameters: { "colsapmple_bytree", "n_estimatiors" } are not used.

[0]	validation_0-auc:0.95169	validation_1-auc:0.92184                                                                  
[1]	validation_0-auc:0.96736	validation_1-auc:0.94032                                                                  
[2]	validation_0-auc:0.97678	validation_1-auc:0.94774                                                                  
[3]	validation_0-auc:0.98136	validation_1-auc:0.95250   

[63]	validation_0-auc:0.99877	validation_1-auc:0.98801                                                                 
[64]	validation_0-auc:0.99877	validation_1-auc:0.98801                                                                 
[14:32:40] WARNING: C:/buildkite-agent/builds/buildkite-windows-cpu-autoscaling-group-i-03de431ba26204c4d-1/xgboost/xgboost-ci-windows/src/learner.cc:767: 
Parameters: { "colsapmple_bytree", "n_estimatiors" } are not used.

[0]	validation_0-auc:0.94622	validation_1-auc:0.90938                                                                  
[1]	validation_0-auc:0.96852	validation_1-auc:0.93047                                                                  
[2]	validation_0-auc:0.97742	validation_1-auc:0.94045                                                                  
[3]	validation_0-auc:0.98185	validation_1-auc:0.94892                                                                  
[4]	validation_0-auc:0.98612	validation_1-auc:0.95371   

[64]	validation_0-auc:0.99925	validation_1-auc:0.98764                                                                 
[65]	validation_0-auc:0.99925	validation_1-auc:0.98764                                                                 
[66]	validation_0-auc:0.99925	validation_1-auc:0.98764                                                                 
[67]	validation_0-auc:0.99925	validation_1-auc:0.98764                                                                 
[68]	validation_0-auc:0.99925	validation_1-auc:0.98764                                                                 
[69]	validation_0-auc:0.99925	validation_1-auc:0.98764                                                                 
[70]	validation_0-auc:0.99925	validation_1-auc:0.98764                                                                 
[71]	validation_0-auc:0.99925	validation_1-auc:0.98764                                                                 
[72]	validation_0-auc:0.99925	validation

[51]	validation_0-auc:0.98504	validation_1-auc:0.96930                                                                 
[52]	validation_0-auc:0.98548	validation_1-auc:0.96963                                                                 
[53]	validation_0-auc:0.98610	validation_1-auc:0.97050                                                                 
[54]	validation_0-auc:0.98650	validation_1-auc:0.97103                                                                 
[55]	validation_0-auc:0.98689	validation_1-auc:0.97178                                                                 
[56]	validation_0-auc:0.98717	validation_1-auc:0.97187                                                                 
[57]	validation_0-auc:0.98748	validation_1-auc:0.97217                                                                 
[58]	validation_0-auc:0.98777	validation_1-auc:0.97252                                                                 
[59]	validation_0-auc:0.98810	validation

...

[93]	validation_0-auc:1.00000	validation_1-auc:0.99344                                                                 
[94]	validation_0-auc:1.00000	validation_1-auc:0.99344                                                                 
[95]	validation_0-auc:1.00000	validation_1-auc:0.99344                                                                 
[96]	validation_0-auc:1.00000	validation_1-auc:0.99344                                                                 
[97]	validation_0-auc:1.00000	validation_1-auc:0.99344                                                                 
[98]	validation_0-auc:1.00000	validation_1-auc:0.99344                                                                 
[99]	validation_0-auc:1.00000	validation_1-auc:0.99344                                                                 
[14:36:35] WARNING: C:/buildkite-agent/builds/buildkite-windows-cpu-autoscaling-group-i-03de431ba26204c4d-1/xgboost/xgboost-ci-windows/src/learner.cc:767: 
Para

[59]	validation_0-auc:1.00000	validation_1-auc:0.99071                                                                 
[60]	validation_0-auc:1.00000	validation_1-auc:0.99080                                                                 
[61]	validation_0-auc:1.00000	validation_1-auc:0.99080                                                                 
[62]	validation_0-auc:1.00000	validation_1-auc:0.99081                                                                 
[63]	validation_0-auc:1.00000	validation_1-auc:0.99078                                                                 
[64]	validation_0-auc:1.00000	validation_1-auc:0.99081                                                                 
[65]	validation_0-auc:1.00000	validation_1-auc:0.99099                                                                 
[66]	validation_0-auc:1.00000	validation_1-auc:0.99104                                                                 
[67]	validation_0-auc:1.00000	validation

[25]	validation_0-auc:0.99908	validation_1-auc:0.98556                                                                 
[26]	validation_0-auc:0.99916	validation_1-auc:0.98679                                                                 
[27]	validation_0-auc:0.99922	validation_1-auc:0.98748                                                                 
[28]	validation_0-auc:0.99927	validation_1-auc:0.98780                                                                 
[29]	validation_0-auc:0.99935	validation_1-auc:0.98790                                                                 
[30]	validation_0-auc:0.99937	validation_1-auc:0.98815                                                                 
[31]	validation_0-auc:0.99940	validation_1-auc:0.98840                                                                 
[32]	validation_0-auc:0.99940	validation_1-auc:0.98873                                                                 
[33]	validation_0-auc:0.99945	validation

[9]	validation_0-auc:0.99523	validation_1-auc:0.97117                                                                  
[10]	validation_0-auc:0.99614	validation_1-auc:0.97372                                                                 
[11]	validation_0-auc:0.99686	validation_1-auc:0.97584                                                                 
[12]	validation_0-auc:0.99713	validation_1-auc:0.97645                                                                 
[13]	validation_0-auc:0.99754	validation_1-auc:0.97799                                                                 
[14]	validation_0-auc:0.99790	validation_1-auc:0.98088                                                                 
[15]	validation_0-auc:0.99822	validation_1-auc:0.98177                                                                 
[16]	validation_0-auc:0.99842	validation_1-auc:0.98254                                                                 
[17]	validation_0-auc:0.99861	validation

[0]	validation_0-auc:0.94989	validation_1-auc:0.91158                                                                  
[1]	validation_0-auc:0.96760	validation_1-auc:0.92789                                                                  
[2]	validation_0-auc:0.97773	validation_1-auc:0.93996                                                                  
[3]	validation_0-auc:0.98202	validation_1-auc:0.94518                                                                  
[4]	validation_0-auc:0.98547	validation_1-auc:0.95016                                                                  
[5]	validation_0-auc:0.98797	validation_1-auc:0.95395                                                                  
[6]	validation_0-auc:0.99057	validation_1-auc:0.95795                                                                  
[7]	validation_0-auc:0.99254	validation_1-auc:0.96283                                                                  
[8]	validation_0-auc:0.99371	validation_

In [154]:
xgb_clf = xgb.XGBClassifier(colsample_bytree=0.7509517286334861, gamma=0.11238303917591316,
                            learning_rate=0.37018445848424064, max_depth=13, min_child_weight=1.0,
                            random_state=109)
xgbo.fit(X_train, y_train)

XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, feature_types=None, gamma=1.5, gpu_id=-1,
              grow_policy='depthwise', importance_type=None,
              interaction_constraints='', learning_rate=0.1, max_bin=256,
              max_cat_threshold=64, max_cat_to_onehot=4, max_delta_step=0,
              max_depth=4, max_leaves=0, min_child_weight=1, missing=nan,
              monotone_constraints='()', n_estimators=100, n_jobs=0,
              num_parallel_tree=1, predictor='auto', random_state=109, ...)

In [155]:
train_pred = xgbo.predict(X_train)
train_proba = xgbo.predict_proba(X_train)

test_pred = xgbo.predict(X_test)
test_proba = xgbo.predict_proba(X_test)

In [156]:
get_clf_eval(y_train, train_pred, train_proba)

오차 행렬
[[5349  700]
 [ 826 6271]]
정확도: 0.8839, 정밀도: 0.8996,     재현율: 0.8836, F1: 0.8915


In [157]:
get_clf_eval(y_test, test_pred, test_proba)

오차 행렬
[[1736  302]
 [ 308 2037]]
정확도: 0.8608, 정밀도: 0.8709,     재현율: 0.8687, F1: 0.8698
